# Интерактивная карта транспорта Москвы
### Геопространственный анализ мультимодальной транспортной инфраструктуры Москвы

In [11]:
import pandas as pd
import folium
from folium import plugins
import numpy as np
import warnings
warnings.filterwarnings('ignore')

## Загрузка и предобработка данных

In [12]:
def load_transport_data():
    datasets = {}
    
    metro = pd.read_csv('data/metro.csv', sep=';', encoding='utf-8', low_memory=False)
    metro['lat'] = pd.to_numeric(metro['Latitude_WGS84'], errors='coerce')
    metro['lon'] = pd.to_numeric(metro['Longitude_WGS84'], errors='coerce')
    datasets['metro'] = metro.dropna(subset=['lat', 'lon'])
    
    railway = pd.read_csv('data/railway.csv', sep=';', encoding='utf-8', low_memory=False)
    railway['lat'] = pd.to_numeric(railway['Latitude_WGS84'], errors='coerce')
    railway['lon'] = pd.to_numeric(railway['Longitude_WGS84'], errors='coerce')
    datasets['railway'] = railway.dropna(subset=['lat', 'lon'])
    
    bus = pd.read_csv('data/bus_station.csv', sep=';', encoding='utf-8', low_memory=False)
    bus['lat'] = pd.to_numeric(bus['Latitude_WGS84'], errors='coerce')
    bus['lon'] = pd.to_numeric(bus['Longitude_WGS84'], errors='coerce')
    datasets['bus'] = bus.dropna(subset=['lat', 'lon'])
    
    bike = pd.read_csv('data/bike_stop.csv', sep=';', encoding='utf-8', low_memory=False)
    bike['lat'] = pd.to_numeric(bike['Latitude_WGS84'], errors='coerce')
    bike['lon'] = pd.to_numeric(bike['Longitude_WGS84'], errors='coerce')
    datasets['bike'] = bike.dropna(subset=['lat', 'lon'])
    
    return datasets

data = load_transport_data()
print(f"Станции метро: {len(data['metro'])}")
print(f"ЖД платформы: {len(data['railway'])}")
print(f"Автобусные станции: {len(data['bus'])}")
print(f"Велопарковки: {len(data['bike'])}")

Станции метро: 1154
ЖД платформы: 276
Автобусные станции: 6
Велопарковки: 1221


## Создание базовой карты

In [13]:
def create_base_map():
    m = folium.Map(
        location=[55.7558, 37.6176],
        zoom_start=10,
        tiles='CartoDB dark_matter'
    )
    
    css = """
    <style>
    @font-face {
        font-family: 'Moscow Sans';
        src: url('MoscowSansRegular.otf') format('opentype');
        font-weight: normal;
    }
    @font-face {
        font-family: 'Moscow Sans';
        src: url('MoscowSansBold.otf') format('opentype');
        font-weight: bold;
    }
    @font-face {
        font-family: 'icomoon';
        src: url('icomoon.ttf') format('truetype');
    }
    
    body, html {
        font-family: 'Moscow Sans', sans-serif !important;
        background-color: #444463 !important;
        color: #fefeff !important;
    }
    
    .leaflet-popup-content-wrapper {
        background: #444463 !important;
        color: #fefeff !important;
        border: 2px solid #72b200 !important;
        border-radius: 8px !important;
        font-family: 'Moscow Sans', sans-serif !important;
    }
    
    .leaflet-popup-tip {
        background: #444463 !important;
        border: 2px solid #72b200 !important;
    }
    
    .leaflet-control-layers {
        background: rgba(68, 68, 99, 0.95) !important;
        color: #fefeff !important;
        border: 2px solid #72b200 !important;
        border-radius: 8px !important;
        font-family: 'Moscow Sans', sans-serif !important;
    }
    
    .leaflet-control-layers label {
        color: #fefeff !important;
        font-family: 'Moscow Sans', sans-serif !important;
    }
    
    .marker-cluster {
        background: #72b200 !important;
        border: 2px solid #fefeff !important;
        color: #444463 !important;
        font-family: 'Moscow Sans', sans-serif !important;
        font-weight: bold !important;
    }
    </style>
    """
    
    m.get_root().html.add_child(folium.Element(css))
    return m

moscow_map = create_base_map()

## Тематический слой 1: Станции метро (кластеризация маркеров)

In [14]:
metro_group = folium.FeatureGroup(name='🚇 Метро', show=True)
metro_cluster = plugins.MarkerCluster(name='Metro Cluster')

for idx, row in data['metro'].iterrows():
    popup_text = f"""
    <div style='font-family: Moscow Sans; color: #fefeff; width: 300px;'>
    <h3 style='color: #72b200; margin: 0;'>🚇 {row.get('Name', 'Станция метро')}</h3>
    <p><strong>Линия:</strong> {row.get('Line', 'Н/Д')}</p>
    <p><strong>Округ:</strong> {row.get('AdmArea', 'Н/Д')}</p>
    <p><strong>Район:</strong> {row.get('District', 'Н/Д')}</p>
    <p><strong>Статус:</strong> {row.get('ObjectStatus', 'Н/Д')}</p>
    </div>
    """
    
    folium.CircleMarker(
        location=[row['lat'], row['lon']],
        radius=6,
        popup=folium.Popup(popup_text, max_width=350),
        color='#dc143c',
        fillColor='#dc143c',
        fillOpacity=0.8,
        weight=2
    ).add_to(metro_cluster)

metro_cluster.add_to(metro_group)
metro_group.add_to(moscow_map)

## Тематический слой 2: ЖД станции (кластеризация маркеров)

In [15]:
railway_group = folium.FeatureGroup(name='🚂 Железная дорога', show=True)
railway_cluster = plugins.MarkerCluster(name='Railway Cluster')

for idx, row in data['railway'].iterrows():
    popup_text = f"""
    <div style='font-family: Moscow Sans; color: #fefeff; width: 300px;'>
    <h3 style='color: #72b200; margin: 0;'>🚂 {row.get('Name', 'ЖД станция')}</h3>
    <p><strong>Направление:</strong> {row.get('RailwayLine', 'Н/Д')}</p>
    <p><strong>Станция:</strong> {row.get('Station', 'Н/Д')}</p>
    <p><strong>Режим работы:</strong> {row.get('WorkingHours', 'Н/Д')}</p>
    </div>
    """
    
    folium.CircleMarker(
        location=[row['lat'], row['lon']],
        radius=5,
        popup=folium.Popup(popup_text, max_width=350),
        color='#228b22',
        fillColor='#228b22',
        fillOpacity=0.7,
        weight=2
    ).add_to(railway_cluster)

railway_cluster.add_to(railway_group)
railway_group.add_to(moscow_map)

## Тематический слой 3: Автобусные станции

In [16]:
bus_group = folium.FeatureGroup(name='🚌 Автобусы', show=False)

for idx, row in data['bus'].iterrows():
    popup_text = f"""
    <div style='font-family: Moscow Sans; color: #fefeff; width: 300px;'>
    <h3 style='color: #72b200; margin: 0;'>🚌 {row.get('Name', 'Автобусная станция')}</h3>
    <p><strong>Адрес:</strong> {row.get('Address', 'Н/Д')}</p>
    <p><strong>Ближайшее метро:</strong> {row.get('MetroStation', 'Н/Д')}</p>
    <p><strong>WiFi:</strong> {row.get('WiFiAvailability', 'Н/Д')}</p>
    </div>
    """
    
    name_str = str(row.get('Name', '')).lower()
    radius = 15 if 'терминал' in name_str or 'вокзал' in name_str else 8
    
    folium.CircleMarker(
        location=[row['lat'], row['lon']],
        radius=radius,
        popup=folium.Popup(popup_text, max_width=350),
        color='#4169e1',
        fillColor='#4169e1',
        fillOpacity=0.6,
        weight=3
    ).add_to(bus_group)

bus_group.add_to(moscow_map)

## Тематический слой 4: Велопарковки (кластеризация маркеров)

In [17]:
bike_group = folium.FeatureGroup(name='🚴 Велопарковки', show=False)
bike_cluster = plugins.MarkerCluster(name='Bike Cluster')

for idx, row in data['bike'].iterrows():
    capacity = row.get('Capacity', 0)
    
    try:
        capacity_num = int(float(str(capacity))) if pd.notna(capacity) and str(capacity).replace('.', '').replace('-', '').isdigit() else 0
        capacity_text = f"{capacity_num} мест" if capacity_num > 0 else "Н/Д"
    except (ValueError, TypeError):
        capacity_text = "Н/Д"
    
    popup_text = f"""
    <div style='font-family: Moscow Sans; color: #fefeff; width: 300px;'>
    <h3 style='color: #72b200; margin: 0;'>🚴 {row.get('Name', 'Велопарковка')}</h3>
    <p><strong>Вместимость:</strong> {capacity_text}</p>
    <p><strong>Округ:</strong> {row.get('AdmArea', 'Н/Д')}</p>
    <p><strong>Район:</strong> {row.get('District', 'Н/Д')}</p>
    </div>
    """
    
    folium.CircleMarker(
        location=[row['lat'], row['lon']],
        radius=4,
        popup=folium.Popup(popup_text, max_width=350),
        color='#ff8c00',
        fillColor='#ff8c00',
        fillOpacity=0.5,
        weight=2
    ).add_to(bike_cluster)

bike_cluster.add_to(bike_group)
bike_group.add_to(moscow_map)

## Тематический слой 5: Тепловая карта плотности транспорта

In [18]:
heat_data = []

for dataset_name, df in data.items():
    if dataset_name in ['metro', 'railway', 'bus', 'bike'] and not df.empty:
        if 'lat' in df.columns and 'lon' in df.columns:
            points = df[['lat', 'lon']].dropna().values.tolist()
            heat_data.extend(points)

heatmap = plugins.HeatMap(
    heat_data,
    name='🔥 Плотность транспорта',
    min_opacity=0.2,
    max_zoom=18,
    radius=20,
    blur=15,
    gradient={0.2: '#444463', 0.4: '#72b200', 0.6: '#a6d400', 0.8: '#d4f400', 1.0: '#ffff00'},
    show=False
)
heatmap.add_to(moscow_map)

## Интерактивные элементы управления

In [19]:
folium.LayerControl(position='topright').add_to(moscow_map)

plugins.Fullscreen(
    position='topleft',
    title='Полноэкранный режим',
    title_cancel='Выход из полноэкранного режима'
).add_to(moscow_map)

minimap = plugins.MiniMap(
    tile_layer='CartoDB dark_matter',
    position='bottomleft',
    width=150,
    height=150
)
minimap.add_to(moscow_map)

plugins.MousePosition(
    position='bottomright',
    separator=' | ',
    empty_string='Н/Д',
    lng_first=False,
    num_digits=4,
    prefix='Координаты:',
    lat_formatter="function(num) {return L.Util.formatNum(num, 4) + ' °С.Ш. ';}",
    lng_formatter="function(num) {return L.Util.formatNum(num, 4) + ' °В.Д.';}"
).add_to(moscow_map)

plugins.MeasureControl(
    position='topleft',
    primary_length_unit='kilometers',
    secondary_length_unit='meters',
    primary_area_unit='sqkilometers',
    secondary_area_unit='sqmeters'
).add_to(moscow_map)

## Экспорт и отображение карты

In [20]:
moscow_map.save('moscow_transport.html')
moscow_map